<a href="https://colab.research.google.com/github/juliaguardiani/test_ITM_BRASIL/blob/main/processing.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install pandas-profiling==3.1.0

In [2]:
!pip install wandb

In [3]:
import wandb
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport
import tempfile
import os

In [4]:
!wandb login --relogin

wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [5]:
# save_code tracking all changes of the notebook and sync with Wandb
run = wandb.init(project="decision_tree", save_code=True)

wandb: Currently logged in as: juliaguardiani. Use `wandb login --relogin` to force relogin


In [6]:
# donwload the latest version of artifact raw_data.csv
artifact = run.use_artifact("decision_tree/preprocessed_data.csv:latest") 

# create a dataframe from the artifact
df_total = pd.read_csv(artifact.file())

In [7]:
df_total.head()

marca_id    marca  antiss    AV    BA    BC  DRML  dresc    DI   EEG  ...  \
0         1   Adidas    0.25  0.25  0.25  0.00  0.25   0.25  0.25  0.25  ...   
1         2  Animale    0.25  0.25  0.00  0.25  0.25   0.25  0.25  0.25  ...   
2         3   Aramis    0.00  0.25  0.00  0.00  0.25   0.25  0.25  0.00  ...   
3         4   Arezzo    0.25  0.25  0.00  0.25  0.00   0.25  0.25  0.25  ...   
4         5    Besni    0.00  0.00  0.00  0.00  0.00   0.00  0.00  0.00  ...   

   SS_02  SMB.1  subc_02  TC_02  TEC_02  TI_02  usuAgua_02  total_01  \
0    0.5    0.5      0.5    0.0     0.5    0.5         0.5      3.50   
1    0.0    0.5      0.0    0.0     0.0    0.5         0.0      3.75   
2    0.5    0.5      0.0    0.0     0.0    0.0         0.5      2.00   
3    0.5    0.5      0.0    0.0     0.0    0.5         0.0      3.25   
4    0.0    0.0      0.0    0.0     0.0    0.0         0.0      0.00   

   total_02  total_03  
0      8.50      14.5  
1      0.00       7.5  
2      1.00       5.5  
3      2.75       6.5  
4      0.00       0.5  

[5 rows x 81 columns]

In [8]:
pip install -U scikit-learn

In [9]:
from sklearn.cluster import KMeans

X = df_total
X_total = X.copy()
X_total.drop(["marca_id", "marca"], axis=1, inplace=True) #eliminando a classe categorica e o seu ID (utilzada apenas como guia)

kmeans = KMeans(n_clusters=3, random_state=0).fit(X_total)
kmeans.labels_

array([0, 2, 2, 2, 1, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 2, 1, 0,
       0, 1, 0, 2, 1, 2, 1, 1, 1, 2, 0, 2, 1, 0, 1, 1, 1, 2, 0, 0, 1, 0,
       0, 1, 1, 1, 0, 0], dtype=int32)

In [10]:
X_total.head()

antiss    AV    BA    BC  DRML  dresc    DI   EEG    EC   ES  ...  SS_02  \
0    0.25  0.25  0.25  0.00  0.25   0.25  0.25  0.25  0.25  0.0  ...    0.5   
1    0.25  0.25  0.00  0.25  0.25   0.25  0.25  0.25  0.00  0.0  ...    0.0   
2    0.00  0.25  0.00  0.00  0.25   0.25  0.25  0.00  0.00  0.0  ...    0.5   
3    0.25  0.25  0.00  0.25  0.00   0.25  0.25  0.25  0.25  0.0  ...    0.5   
4    0.00  0.00  0.00  0.00  0.00   0.00  0.00  0.00  0.00  0.0  ...    0.0   

   SMB.1  subc_02  TC_02  TEC_02  TI_02  usuAgua_02  total_01  total_02  \
0    0.5      0.5    0.0     0.5    0.5         0.5      3.50      8.50   
1    0.5      0.0    0.0     0.0    0.5         0.0      3.75      0.00   
2    0.5      0.0    0.0     0.0    0.0         0.5      2.00      1.00   
3    0.5      0.0    0.0     0.0    0.5         0.0      3.25      2.75   
4    0.0      0.0    0.0     0.0    0.0         0.0      0.00      0.00   

   total_03  
0      14.5  
1       7.5  
2       5.5  
3       6.5  
4       0.5  

[5 rows x 79 columns]

In [11]:
 X_total['label'] = kmeans.predict(X_total)

In [12]:
X_total.head()

antiss    AV    BA    BC  DRML  dresc    DI   EEG    EC   ES  ...  SMB.1  \
0    0.25  0.25  0.25  0.00  0.25   0.25  0.25  0.25  0.25  0.0  ...    0.5   
1    0.25  0.25  0.00  0.25  0.25   0.25  0.25  0.25  0.00  0.0  ...    0.5   
2    0.00  0.25  0.00  0.00  0.25   0.25  0.25  0.00  0.00  0.0  ...    0.5   
3    0.25  0.25  0.00  0.25  0.00   0.25  0.25  0.25  0.25  0.0  ...    0.5   
4    0.00  0.00  0.00  0.00  0.00   0.00  0.00  0.00  0.00  0.0  ...    0.0   

   subc_02  TC_02  TEC_02  TI_02  usuAgua_02  total_01  total_02  total_03  \
0      0.5    0.0     0.5    0.5         0.5      3.50      8.50      14.5   
1      0.0    0.0     0.0    0.5         0.0      3.75      0.00       7.5   
2      0.0    0.0     0.0    0.0         0.5      2.00      1.00       5.5   
3      0.0    0.0     0.0    0.5         0.0      3.25      2.75       6.5   
4      0.0    0.0     0.0    0.0         0.0      0.00      0.00       0.5   

   label  
0      0  
1      2  
2      2  
3      2  
4      1  

[5 rows x 80 columns]

In [14]:
ProfileReport(X_total, title="Pandas Profiling Report", explorative=True)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [13]:
X_total.to_csv('cluster_total.csv',index=False)

In [14]:
input_artifact="decision_tree/ITM_BRASIL_2021_data.csv:latest"
artifact_name="cluster_total.csv"
artifact_type="kmeans_data"
artifact_description="Data after preprocessing"

In [15]:
# Create a new artifact and configure with the necessary arguments
artifact = wandb.Artifact(name=artifact_name,
                          type=artifact_type,
                          description=artifact_description)
artifact.add_file(artifact_name)

<ManifestEntry digest: tnDhKYMSpEGCpUw84V2Ucg==>

In [16]:
run.log_artifact(artifact)

In [17]:
run.finish()